In [1]:
import numpy as np
import random
import math
from typing import Tuple, Literal, Union, Optional, List, Dict, NamedTuple, Callable, Any, Set
from queue import Queue
import warnings
import sys
import json
import time
import types
import pickle
import plotly.graph_objs as go
import plotly.express as px
import pandas as pd
import os
from eoh.problems.optimization.classic_benchmark_path_planning.utils.benchmark import MultiMapBenchmarker

In [2]:
pd.set_option('display.max_rows', None)     # 모든 행 표시
pd.set_option('display.max_columns', None)  # 모든 열 표시
pd.set_option('display.width', None)        # 가로 폭 제한 없음
pd.set_option('display.max_colwidth', None) # 셀 내용 잘림 없이 표시

In [3]:
class Map(NamedTuple):
    grid: np.ndarray
    start: Union[Tuple[float, float], Tuple[float, float, float]]
    goal: Union[Tuple[float, float], Tuple[float, float, float]]
    obstacles: List[Union[Tuple[float, float, float, float], Tuple[float, float, float, float, float, float]]] # x, y, width, height or x, y, z, width, height, dimension
    size: Union[Tuple[int, int], Tuple[int, int, int]]

class PlannerResult(NamedTuple):
    success: bool
    path: List[Union[Tuple[float, float], Tuple[float, float, float]]]
    nodes: List[Union[Tuple[float, float], Tuple[float, float, float]]]
    edges: List[Tuple[Tuple[float, ...], Tuple[float, ...]]]  # (parent, child)

class Node:
    def __init__(self, position, parent=None, cost=0.0):
        self.position = position
        self.parent = parent
        self.cost = cost
        self.children = []
        self.valid = True  # 장애물 충돌 여부 등


In [4]:
def visualize_map_shapes(
    map_array: np.ndarray,
    start: Optional[Tuple[int, ...]] = None,
    goal: Optional[Tuple[int, ...]] = None,
    obs:List[Tuple[int, ...]] = None,
    path: Optional[List[Tuple[float, ...]]] = None,
    nodes: Optional[List[Tuple[float, ...]]] = None,
    edges: Optional[List[Tuple[float, ...]]] = None,
    title: str = "Map Visualization"
):
    fig = go.Figure()

    if map_array.ndim == 2:
        height, width = map_array.shape
        
        for x, y, w, h in obs:
                fig.add_shape(
                    type="rect",
                    x0=x, x1=x+w, y0=y, y1=y+h,
                    fillcolor="purple",opacity=0.5,
                    line=dict(width=0)
                )

        # 방문 노드
        if nodes:
            vx, vy = zip(*nodes)
            fig.add_trace(go.Scatter(
                x=vx, y=vy, mode="markers",
                marker=dict(size=4, color="blue"),
                name="nodes"
            ))

        # 경로
        if path:
            px, py = zip(*path)
            fig.add_trace(go.Scatter(
                x=px, y=py, mode="lines+markers",
                line=dict(color="green"),
                marker=dict(size=6),
                name="Path"
            ))

        # 엣지 (연결 정보)
        if edges:
            for parent, child in edges:
                fig.add_trace(go.Scatter(
                    x=[parent.position[0], child.position[0]], y=[parent.position[1], child.position[1]],
                    mode="lines",
                    line=dict(color="lightblue", width=1),
                    showlegend=False,
                    hoverinfo="skip"
                ))


        # 시작/목표
        if start:
            fig.add_trace(go.Scatter(
                x=[start[0]], y=[start[1]], mode="markers",
                marker=dict(size=10, color="red"),
                name="Start"
            ))

        if goal:
            fig.add_trace(go.Scatter(
                x=[goal[0]], y=[goal[1]], mode="markers",
                marker=dict(size=10, color="orange"),
                name="Goal"
            ))

        fig.add_shape(
            type="rect",
            x0=0, y0=0,
            x1=width, y1=height,
            line=dict(color="white", width=3),
            fillcolor="rgba(0,0,0,0)",  # 투명 내부
            layer="above"
        )

        fig.update_layout(
            title=title,
            xaxis=dict(scaleanchor="y", showgrid=False),
            # yaxis=dict(showgrid=False, autorange="reversed"),
            yaxis=dict(showgrid=False),
            height=600, width=600
        )

    elif map_array.ndim == 3:
        z, y, x = map_array.nonzero()
        x, y, z = list(x), list(y), list(z)

        # for x,y,w,h in obs:
        #     fig.add_trace(go.Mesh3d(
        #         x=x, y=y, z=z,
        #         color='black',
        #         opacity=1.0,
        #         alphahull=0,
        #         name='Obstacles'
        #     ))

        fig.add_trace(go.Mesh3d(
            x=x, y=y, z=z,
            color='black',
            opacity=1.0,
            alphahull=0,
            name='Obstacles'
        ))

        if nodes:
            vx, vy, vz = zip(*nodes)
            fig.add_trace(go.Scatter3d(
                x=vx, y=vy, z=vz,
                mode='markers',
                marker=dict(size=2, color='blue'),
                name='Visited'
            ))

        # 엣지 (연결 정보)
        if edges:
            for parent, child in edges:
                fig.add_trace(go.Scatter3d(
                    x=[parent.position[0], child.position[0]],
                    y=[parent[1].position, child.position[1]],
                    z=[parent[2].position, child.position[2]],
                    mode='lines',
                    line=dict(color='lightblue', width=2),
                    showlegend=False,
                    hoverinfo="skip"
                ))

        if path:
            px_, py_, pz_ = zip(*path)
            fig.add_trace(go.Scatter3d(
                x=px_, y=py_, z=pz_,
                mode='lines+markers',
                marker=dict(size=3, color='green'),
                name='Path'
            ))

        if start:
            fig.add_trace(go.Scatter3d(
                x=[start[0]], y=[start[1]], z=[start[2]],
                mode='markers',
                marker=dict(size=5, color='red'),
                name='Start'
            ))

        if goal:
            fig.add_trace(go.Scatter3d(
                x=[goal[0]], y=[goal[1]], z=[goal[2]],
                mode='markers',
                marker=dict(size=5, color='orange'),
                name='Goal'
            ))

        fig.update_layout(
            title=title,
            scene=dict(aspectmode='data'),
            height=700, width=700
        )

        

    fig.show()


In [5]:
class MapIO:
    @staticmethod
    def save_map(map_data: Map, filename: str) -> None:
        """Save Map object to a binary file."""
        with open(filename, 'wb') as f:
            pickle.dump(map_data, f)

    @staticmethod
    def load_map(filename: str) -> Map:
        """Load Map object from a binary file."""
        if not os.path.exists(filename):
            raise FileNotFoundError(f"Map file not found: {filename}")
        with open(filename, 'rb') as f:
            return pickle.load(f)

In [6]:
raw_maps = ["Maze_map_easy.pkl", "Narrow_map.pkl", "Multi_obs_map.pkl"]

multi_obs_map = MapIO.load_map("Multi_obs_map.pkl")
print("Start:", multi_obs_map.start)
print("Obstacles:", len(multi_obs_map.obstacles))
print(multi_obs_map.grid.shape)

hard_maze_map = MapIO.load_map("Maze_map.pkl")
print("Start:", hard_maze_map.start)
print("Obstacles:", len(hard_maze_map.obstacles))
print(hard_maze_map.grid.shape)

maze_map = MapIO.load_map("Maze_map_easy.pkl")
print("Start:", maze_map.start)
print("Obstacles:", len(maze_map.obstacles))
print(maze_map.grid.shape)

narrow_map = MapIO.load_map("Narrow_map.pkl")
print("Start:", narrow_map.start)
print("Obstacles:", len(narrow_map.obstacles))
print(narrow_map.grid.shape)

Start: (1, 1)
Obstacles: 35
(100, 100)
Start: (29, 40)
Obstacles: 8
(100, 100)
Start: (29, 10)
Obstacles: 5
(100, 100)
Start: (80, 50)
Obstacles: 5
(100, 100)


In [7]:
maps=[multi_obs_map, maze_map, narrow_map]

In [8]:
json_path = './eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/classic_method__.json'
with open(json_path, "r") as f:
    classic_method = json.load(f)

print(classic_method[0].keys())

dict_keys(['algorithm', 'algorithm_description', 'planning_mechanism', 'code'])


In [9]:
import_string ='''
from typing import Tuple, Literal, Union, Optional, List, Dict, NamedTuple, Callable, Any, Set, TYPE_CHECKING, Type
import time
from queue import Queue
import numpy as np
import random
import math
import sys
import os
from eoh.problems.optimization.classic_benchmark_path_planning.utils.architecture_utils import PlannerResult, Map
'''

In [10]:
def get_exp_result(path, ref_avg):
    with open(path, "r") as f:
        data = json.load(f)
        filtered_sorted_algorithms = sorted(
        [alg for alg in data if alg.get('operator') != 'initial'],
        key=lambda x: x.get('objective', float('inf'))
        )

    len(filtered_sorted_algorithms)

    # ref_avg 앞에서 선언됨
    maps = [multi_obs_map, maze_map, narrow_map]
    benchmarker = MultiMapBenchmarker(maps=maps, iter=100)

    g_total_df = pd.DataFrame()

    for method in filtered_sorted_algorithms:
        code_string = method['code']
        namedf = pd.DataFrame()
        namedf['alg_name'] = [method['objective']]* len(maps)
        with warnings.catch_warnings():
            warnings.simplefilter("ignore")
            planning_module = types.ModuleType("planning_module")
            exec(import_string+code_string, planning_module.__dict__)
            sys.modules[planning_module.__name__] = planning_module
            try:
                planner = planning_module.Planner(max_iter=5000)
            except:
                continue
            res, avg_rest = benchmarker.run(planner.plan)

            if avg_rest is None: continue
            imp_res = MultiMapBenchmarker.get_improvement(ref_avg, avg_rest)

            res_df = pd.concat([namedf, avg_rest, imp_res], axis=1)
            g_total_df = pd.concat([g_total_df, res_df], axis=0)

    return g_total_df

In [11]:
maps = [multi_obs_map, maze_map, narrow_map]
benchmarker = MultiMapBenchmarker(maps=maps, iter=100)

total_df = pd.DataFrame()

for method in classic_method:
    code_string = method['code']
    namedf = pd.DataFrame()
    namedf['alg_name'] = [method['algorithm']]* len(maps)
    with warnings.catch_warnings():
        warnings.simplefilter("ignore")
        planning_module = types.ModuleType("planning_module")
        exec(import_string+code_string, planning_module.__dict__)
        sys.modules[planning_module.__name__] = planning_module
        planner = planning_module.Planner(max_iter=5000)
        res, avg_rest = benchmarker.run(planner.plan)
        if method['algorithm'] == 'RRT':
            ref_avg = avg_rest
            
        if avg_rest is None: continue
        imp_res = MultiMapBenchmarker.get_improvement(ref_avg, avg_rest)

        res_df = pd.concat([namedf, avg_rest, imp_res], axis=1)
        total_df = pd.concat([total_df, res_df], axis=0)

total_df


[2025.09.17 - 13:19:51] Map 1
Iteration 1: Time taken: 0.0243 seconds, Success: True
Iteration 2: Time taken: 0.0258 seconds, Success: True
Iteration 3: Time taken: 0.0193 seconds, Success: True
Iteration 4: Time taken: 0.0197 seconds, Success: True
Iteration 5: Time taken: 0.0132 seconds, Success: True
Iteration 6: Time taken: 0.0103 seconds, Success: True
Iteration 7: Time taken: 0.0083 seconds, Success: True
Iteration 8: Time taken: 0.0557 seconds, Success: True
Iteration 9: Time taken: 0.0268 seconds, Success: True
Iteration 10: Time taken: 0.0469 seconds, Success: True
Iteration 11: Time taken: 0.0218 seconds, Success: True
Iteration 12: Time taken: 0.0303 seconds, Success: True
Iteration 13: Time taken: 0.0217 seconds, Success: True
Iteration 14: Time taken: 0.0489 seconds, Success: True
Iteration 15: Time taken: 0.0284 seconds, Success: True
Iteration 16: Time taken: 0.0167 seconds, Success: True
Iteration 17: Time taken: 0.0167 seconds, Success: True
Iteration 18: Time taken: 0

alg_name  map_id  success_rate  time_avg  num_nodes_avg  \
0                          RRT       0           1.0  0.034087         461.98   
1                          RRT       1           1.0  0.204536        1637.59   
2                          RRT       2           1.0  0.069425         859.41   
0                         RRT*       0           1.0  0.071971         447.98   
1                         RRT*       1           1.0  0.417879        1630.00   
2                         RRT*       2           1.0  0.126314         796.67   
0                  RRT-Connect       0           1.0  0.009053         106.12   
1                  RRT-Connect       1           1.0  0.015629         236.56   
2                  RRT-Connect       2           1.0  0.019998         251.01   
0                 RRT*-Connect       0           1.0  0.011713         129.62   
1                 RRT*-Connect       1           1.0  0.019507         263.17   
2                 RRT*-Connect       2           1.0  0.028773         288.33   
0                       BI-RRT       0           1.0  0.003243          72.90   
1                       BI-RRT       1           1.0  0.009484         228.86   
2                       BI-RRT       2           1.0  0.007953         163.75   
0                      BI-RRT*       0           1.0  0.019014          83.31   
1                      BI-RRT*       1           1.0  0.034051         240.33   
2                      BI-RRT*       2           1.0  0.029838         203.75   
0                Informed-RRT*       0           1.0  0.294471         726.89   
1                Informed-RRT*       1           1.0  0.360581        1218.83   
2                Informed-RRT*       2           1.0  0.187567         845.48   
0        Informed-RRT*-Connect       0           1.0  0.810143         471.14   
1        Informed-RRT*-Connect       1           1.0  0.445213         589.12   
2        Informed-RRT*-Connect       2           1.0  0.616257         563.16   
0  Bidirectional-Informed-RRT*       0           1.0  0.195019         440.85   
1  Bidirectional-Informed-RRT*       1           1.0  0.102855         508.97   
2  Bidirectional-Informed-RRT*       2           1.0  0.140451         551.00   
0        Improved-RRT*-Connect       0           1.0  0.143102         334.00   
1        Improved-RRT*-Connect       1           1.0  0.139353         644.38   
2        Improved-RRT*-Connect       2           1.0  0.144812         578.11   

   path_length_avg  smoothness_avg  success_improvement  time_improvement  \
0       188.080816        0.006254                  0.0         -0.000000   
1       303.968509        0.003852                  0.0         -0.000000   
2       150.713378        0.007887                  0.0         -0.000000   
0       157.771191        0.014527                  0.0       -111.140139   
1       225.665909        0.011059                  0.0       -104.305886   
2       116.530178        0.021042                  0.0        -81.944086   
0       195.985942        0.011055                  0.0         73.440351   
1       302.131675        0.007242                  0.0         92.358969   
2       160.833474        0.014351                  0.0         71.194328   
0       171.903015        0.016822                  0.0         65.636578   
1       258.288269        0.011071                  0.0         90.463035   
2       133.799123        0.021584                  0.0         58.555265   
0       179.646964        0.010684                  0.0         90.485633   
1       305.361103        0.006401                  0.0         95.363138   
2       156.816038        0.013011                  0.0         88.544304   
0       165.592398        0.018017                  0.0         44.219158   
1       264.277359        0.010454                  0.0         83.352227   
2       130.651560        0.022292                  0.0         57.020928   
0       149.971162        0.029144             

In [12]:
# classic method result
grouped_avg = total_df.groupby('alg_name').mean()
a = pd.DataFrame(grouped_avg)
a

map_id  success_rate  time_avg  num_nodes_avg  \
alg_name                                                                     
BI-RRT                          1.0           1.0  0.006893     155.170000   
BI-RRT*                         1.0           1.0  0.027634     175.796667   
Bidirectional-Informed-RRT*     1.0           1.0  0.146108     500.273333   
Improved-RRT*-Connect           1.0           1.0  0.142422     518.830000   
Informed-RRT*                   1.0           1.0  0.280873     930.400000   
Informed-RRT*-Connect           1.0           1.0  0.623871     541.140000   
RRT                             1.0           1.0  0.102683     986.326667   
RRT*                            1.0           1.0  0.205388     958.216667   
RRT*-Connect                    1.0           1.0  0.019998     227.040000   
RRT-Connect                     1.0           1.0  0.014893     197.896667   

                             path_length_avg  smoothness_avg  \
alg_name                                                       
BI-RRT                            213.941368        0.010032   
BI-RRT*                           186.840439        0.016921   
Bidirectional-Informed-RRT*       171.859631        0.029741   
Improved-RRT*-Connect             170.811093        0.030153   
Informed-RRT*                     161.982690        0.030676   
Informed-RRT*-Connect             165.450936        0.044705   
RRT                               214.254234        0.005997   
RRT*                              166.655759        0.015543   
RRT*-Connect                      187.996802        0.016492   
RRT-Connect                       219.650364        0.010883   

                             success_improvement  time_improvement  \
alg_name                                                             
BI-RRT                                       0.0         91.464358   
BI-RRT*                                      0.0         61.530771   
Bidirectional-Informed-RRT*                  0.0       -174.904930   
Improved-RRT*-Connect                        0.0       -132.177840   
Informed-RRT*                                0.0       -336.781488   
Informed-RRT*-Connect                        0.0      -1060.673000   
RRT                                          0.0          0.000000   
RRT*                                         0.0        -99.130037   
RRT*-Connect                                 0.0         71.551626   
RRT-Connect                                  0.0         78.997883   

                             node_improvement  length_improvement  \
alg_name                                                            
BI-RRT                              83.730304           -0.007719   
BI-RRT*                             81.194264           12.775225   
Bidirectional-Informed-RRT*         36.459870           19.815096   
Improved-RRT*-Connect               40.361656           19.889434   
Informed-RRT*                      -10.049902           23.838074   
Informed-RRT*-Connect               32.171246           22.505155   
RRT                                  0.000000            0.000000   
RRT*                                 3.598092           21.518749   
RRT*-Connect                        74.107393           11.617421   
RRT-Connect                         77.792148           -3.437853   

                             smoothness_improvement  objective_score  
alg_name                                                              
BI-RRT                                    67.326861        27.771310  
BI-RRT*                                  180.716786        27.027950  
Bidirectional-Informed-RRT*              389.512360       -38.634860  
Improved-RRT*-Connect                    394.092078       -25.749231  
Informed-RRT*                            415.824461       -84.652480  
Informed-RRT*-Connect                    634.562555      -301.525994  
RRT                                        0.000000         0.000000  
RRT*          

In [13]:
exp_path_dict = dict()
exp_path_dict['eoh'] = "./path_planning/exp_result/basic_eoh_from_ma.json"
exp_path_dict['expert'] = "./path_planning/mobj/results/pops/population_generation_9.json"
exp_path_dict['analysis'] = "./path_planning/mobj_analysis/results/pops/population_generation_15.json"
exp_path_dict['ma1'] = "./paper_result/interactive_multi_agent1/results/pops/population_generation_8.json"
exp_path_dict['ma2'] = "./paper_result/interactive_multi_agent2/results/pops/population_generation_10.json"
exp_path_dict['ma3'] = "./paper_result/interactive_multi_agent3/results/pops/population_generation_15.json"
exp_path_dict['ma4'] = "./paper_result/interactive_multi_agent4/results/pops/population_generation_15.json"
exp_path_dict['ma5'] = "./paper_result/interactive_multi_agent5/results/pops/population_generation_23.json"

In [14]:
result_dfs = {}

for k, path in exp_path_dict.items():
    res = get_exp_result(path, ref_avg)
    result_dfs[k] = res

[2025.09.17 - 13:41:58] Map 1
Iteration 1: Time taken: 0.0000 seconds, Success: True
Iteration 2: Time taken: 0.0195 seconds, Success: True
Iteration 3: Time taken: 0.0080 seconds, Success: True
Iteration 4: Time taken: 0.0151 seconds, Success: True
Iteration 5: Time taken: 0.0000 seconds, Success: True
Iteration 6: Time taken: 0.0160 seconds, Success: True
Iteration 7: Time taken: 0.0049 seconds, Success: True
Iteration 8: Time taken: 0.0000 seconds, Success: True
Iteration 9: Time taken: 0.0096 seconds, Success: True
Iteration 10: Time taken: 0.0000 seconds, Success: True
Iteration 11: Time taken: 0.0207 seconds, Success: True
Iteration 12: Time taken: 0.0010 seconds, Success: True
Iteration 13: Time taken: 0.0120 seconds, Success: True
Iteration 14: Time taken: 0.0147 seconds, Success: True
Iteration 15: Time taken: 0.0000 seconds, Success: True
Iteration 16: Time taken: 0.0000 seconds, Success: True
Iteration 17: Time taken: 0.0167 seconds, Success: True
Iteration 18: Time taken: 0

In [16]:
frames = list()
raw_frames = list()

for k, df in result_dfs.items():
    grouped_df = df.groupby('alg_name').mean()
    grouped_df['method'] = k
    frames.append(grouped_df)
    df['method'] = k
    raw_frames.append(df)

merged_df = pd.concat(frames, ignore_index=True)
raw_merged_df = pd.concat(raw_frames, ignore_index=True)

In [19]:
a

map_id  success_rate  time_avg  num_nodes_avg  \
alg_name                                                                     
BI-RRT                          1.0           1.0  0.006893     155.170000   
BI-RRT*                         1.0           1.0  0.027634     175.796667   
Bidirectional-Informed-RRT*     1.0           1.0  0.146108     500.273333   
Improved-RRT*-Connect           1.0           1.0  0.142422     518.830000   
Informed-RRT*                   1.0           1.0  0.280873     930.400000   
Informed-RRT*-Connect           1.0           1.0  0.623871     541.140000   
RRT                             1.0           1.0  0.102683     986.326667   
RRT*                            1.0           1.0  0.205388     958.216667   
RRT*-Connect                    1.0           1.0  0.019998     227.040000   
RRT-Connect                     1.0           1.0  0.014893     197.896667   

                             path_length_avg  smoothness_avg  \
alg_name                                                       
BI-RRT                            213.941368        0.010032   
BI-RRT*                           186.840439        0.016921   
Bidirectional-Informed-RRT*       171.859631        0.029741   
Improved-RRT*-Connect             170.811093        0.030153   
Informed-RRT*                     161.982690        0.030676   
Informed-RRT*-Connect             165.450936        0.044705   
RRT                               214.254234        0.005997   
RRT*                              166.655759        0.015543   
RRT*-Connect                      187.996802        0.016492   
RRT-Connect                       219.650364        0.010883   

                             success_improvement  time_improvement  \
alg_name                                                             
BI-RRT                                       0.0         91.464358   
BI-RRT*                                      0.0         61.530771   
Bidirectional-Informed-RRT*                  0.0       -174.904930   
Improved-RRT*-Connect                        0.0       -132.177840   
Informed-RRT*                                0.0       -336.781488   
Informed-RRT*-Connect                        0.0      -1060.673000   
RRT                                          0.0          0.000000   
RRT*                                         0.0        -99.130037   
RRT*-Connect                                 0.0         71.551626   
RRT-Connect                                  0.0         78.997883   

                             node_improvement  length_improvement  \
alg_name                                                            
BI-RRT                              83.730304           -0.007719   
BI-RRT*                             81.194264           12.775225   
Bidirectional-Informed-RRT*         36.459870           19.815096   
Improved-RRT*-Connect               40.361656           19.889434   
Informed-RRT*                      -10.049902           23.838074   
Informed-RRT*-Connect               32.171246           22.505155   
RRT                                  0.000000            0.000000   
RRT*                                 3.598092           21.518749   
RRT*-Connect                        74.107393           11.617421   
RRT-Connect                         77.792148           -3.437853   

                             smoothness_improvement  objective_score  
alg_name                                                              
BI-RRT                                    67.326861        27.771310  
BI-RRT*                                  180.716786        27.027950  
Bidirectional-Informed-RRT*              389.512360       -38.634860  
Improved-RRT*-Connect                    394.092078       -25.749231  
Informed-RRT*                            415.824461       -84.652480  
Informed-RRT*-Connect                    634.562555      -301.525994  
RRT                                        0.000000         0.000000  
RRT*          

In [ ]:
merged_df.sort_values(by='objective_score', ascending=False)

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
29      1.0      1.000000  0.016132     186.743333       173.716691   
113     1.0      1.000000  0.019465     209.756667       172.449503   
111     1.0      1.000000  0.019509     201.826667       172.328341   
110     1.0      1.000000  0.018454     198.183333       173.003572   
112     1.0      1.000000  0.020019     207.730000       172.661390   
120     1.0      1.000000  0.019827     204.806667       173.492348   
34      1.0      1.000000  0.016451     173.316667       174.881976   
122     1.0      1.000000  0.019666     208.053333       173.409424   
121     1.0      1.000000  0.020577     210.430000       173.089159   
51      1.0      1.000000  0.018327     179.866667       174.346756   
52      1.0      1.000000  0.016048     173.070000       175.479314   
40      1.0      1.000000  0.017778     190.186667       173.824895   
35      1.0      1.000000  0.018441     174.963333       174.876281   
49      1.0      1.000000  0.019066     176.073333       174.644393   
48      1.0      1.000000  0.018596     179.343333       175.884721   
150     1.0      1.000000  0.018011     225.100000       174.043268   
66      1.0      1.000000  0.017439     180.440000       176.444869   
65      1.0      1.000000  0.019160     180.816667       174.642750   
37      1.0      1.000000  0.018308     185.733333       175.251277   
32      1.0      1.000000  0.020144     178.890000       172.272975   
42      1.0      1.000000  0.018859     180.173333       174.883445   
41      1.0      1.000000  0.019070     179.670000       173.781344   
46      1.0      1.000000  0.015908     158.873333       177.732050   
43      1.0      1.000000  0.020303     179.606667       172.820324   
56      1.0      1.000000  0.018782     176.023333       175.795751   
50      1.0      1.000000  0.020660     183.200000       173.587014   
71      1.0      1.000000  0.019593     176.050000       174.714185   
53      1.0      1.000000  0.018661     175.990000       174.294742   
131     1.0      1.000000  0.018698     185.146667       174.556705   
47      1.0      1.000000  0.020411     184.626667       172.470598   
59      1.0      1.000000  0.020613     182.686667       173.840769   
36      1.0      1.000000  0.020011     187.816667       173.992295   
39      1.0      1.000000  0.021424     188.423333       172.496103   
55      1.0      1.000000  0.020819     182.773333       173.400960   
114     1.0      1.000000  0.023068     238.176667       174.970997   
62      1.0      1.000000  0.022204     190.270000       173.332603   
182     1.0      1.000000  0.022286     182.300000       173.924949   
38      1.0      1.000000  0.024988     237.686667       174.230273   
63      1.0      1.000000  0.022438     190.893333       175.062536   
58      1.0      1.000000  0.019077     166.823333       177.586252   
123     1.0      1.000000  0.021822     210.623333       172.204986   
117     1.0      1.000000  0.021043     183.460000       178.594818   
23      1.0      1.000000  0.017515     147.726667       178.011394   
149     1.0      1.000000  0.023122     316.660000       174.402637   
137     1.0      1.000000  0.022684     221.450000       173.228831   
115     1.0      1.000000  0.022735     222.823333       171.802445   
45      1.0      1.000000  0.017330     181.693333       175.948103   
68      1.0      1.000000  0.023174     198.916667       173.578301   
129     1.0      1.000000  0.024065     240.853333       174.476217   
128     1.0      1.000000  0.020416     167.130000       180.297996   
21      1.0      1.000000  0.014836     144.276667       179.050676   
82      1.0      1.000000  0.021114     233.163333       176.138664   
31      1.0      1.000000  0.018265     149.080000       177.898852   
151     1.0      1.000000  0.025775     251.136667       174.262257   
44      1.0      1.000000  0.019320     190.190000       176.008898   
61      1.0      0.996667  0.

In [25]:
raw_merged_df[raw_merged_df['map_id']==1].sort_values(by='objective_score', ascending=False)

alg_name  map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
448 -36.43867       1          1.00  0.022968         370.29       235.651696   
88   -6.33180       1          1.00  0.023003         283.44       237.711584   
337 -38.53073       1          1.00  0.022427         271.46       234.354771   
562 -33.96721       1          1.00  0.025985         205.25       236.202128   
331 -39.02046       1          1.00  0.021801         261.93       233.935687   
364 -35.51213       1          1.00  0.022485         265.38       235.581061   
334 -38.54314       1          1.00  0.023176         260.75       233.665943   
367 -35.47883       1          1.00  0.022166         269.57       234.869617   
385 -34.04928       1          1.00  0.021357         197.20       241.260555   
340 -38.01395       1          1.00  0.025639         290.50       234.096302   
349 -37.13607       1          1.00  0.025588         312.73       235.879855   
547 -37.48589       1          1.00  0.023193         217.90       234.759833   
343 -37.67647       1          1.00  0.026238         295.22       235.491473   
361 -35.65902       1          1.00  0.022857         267.40       235.265488   
352 -36.65222       1          1.00  0.023851         223.43       237.807524   
433 -29.96541       1          1.00  0.031352         262.32       235.391827   
388 -33.90720       1          1.00  0.026786         292.21       234.388157   
451 -36.26177       1          1.00  0.019717         278.74       234.833310   
439 -29.65900       1          1.00  0.033379         292.33       237.696705   
394 -33.51759       1          1.00  0.020730         234.23       234.479866   
454 -34.89579       1          1.00  0.031199         319.23       233.942429   
226 -35.41092       1          1.00  0.035104         364.50       237.179546   
499 -28.64627       1          1.00  0.033792         227.57       237.804329   
412 -32.08129       1          1.00  0.024385         275.56       233.025342   
379 -34.19888       1          1.00  0.026589         296.07       232.904517   
511 -24.54042       1          1.00  0.024423         171.34       240.134525   
397 -32.98846       1          1.00  0.032210         291.18       238.453228   
121 -27.62859       1          1.00  0.019188         230.69       236.047952   
565 -33.94541       1          1.00  0.025214         182.24       237.505879   
154 -26.35191       1          1.00  0.021562         238.50       237.854752   
139 -26.65888       1          1.00  0.017632         195.54       239.621382   
145 -26.55806       1          1.00  0.023193         233.42       239.546759   
112 -28.18988       1          1.00  0.020793         239.16       238.824856   
202 -25.04421       1          1.00  0.022946         297.33       239.009679   
199 -25.13323       1          1.00  0.020071         231.44       239.437783   
148 -26.54166       1          1.00  0.023858         238.06       238.287959   
175 -25.77476       1          1.00  0.018959         191.42       239.258532   
370 -35.05016       1          1.00  0.026201         281.63       231.038856   
160 -26.11907       1          1.00  0.021155         220.84       235.392987   
109 -28.86429       1          1.00  0.020351         228.53       236.468713   
196 -25.36826       1          1.00  0.022748         237.74       237.577279   
424 -31.40894       1          1.00  0.027866         243.81       232.278494   
442 -28.94013       1          1.00  0.031556         291.99       234.142778   
106 -29.37349       1          1.00  0.022429         229.37       239.185670   
124 -27.52708       1          1.00  0.023148         234.93       235.398456   
346 -37.37284       1          1.00  0.026016         287.02       231.054197   
142 -26.62690       1          1.00  0.021588         223.52       234.550233   
214 -24.75582       1          1.00  0.023575         228.78       237.358061   
184 -25.56803       1          1.00 